# f0 Sonification
This notebook illustrates the functionallity...

In [1]:
import numpy as np
import pandas as pd
import os
import librosa
from IPython import display as ipd

from libsoni.core import f0
from libsoni.util.utils import mix_sonification_and_original


Fs= 22050

## Simple Use Case: C Major Triad

In [2]:
C_Major_Triad_f0 = [261.63, 329.63, 392.00, 523.25, 0.0]

# Starting time position of the first annotation (f0=261.63)
start_sec = 0.2

# Duration of each f0 value in seconds
step_sec = 0.5

time_positions = np.arange(start_sec, len(C_Major_Triad_f0) * step_sec, step_sec)
time_f0 = np.column_stack((time_positions, C_Major_Triad_f0))

print('\nThe sonification function takes a 2-D numpy array comprising starting time positions and f0 values e.g.,:\n')
print('-------------------------')
print('    Start   |     f0     ')
print('-------------------------')
for row in time_f0:
    print('    %.2f    |   %.2f   ' % (row[0], row[1]))


The sonification function takes a 2-D numpy array comprising starting time positions and f0 values e.g.,:

-------------------------
    Start   |     f0     
-------------------------
    0.20    |   261.63   
    0.70    |   329.63   
    1.20    |   392.00   
    1.70    |   523.25   
    2.20    |   0.00   


#### Sonified C Major Triad

In [3]:
sonified_C_Major_Triad_f0 = f0.sonify_f0(time_f0=time_f0, fs=Fs)
ipd.display(ipd.Audio(sonified_C_Major_Triad_f0, rate=Fs))

#### The user can set the partials and their amplitudes


In [4]:
custom_partials = np.array([1,2,3,4,5])
custom_partials_amplitudes = np.array([1/1,1/2,1/3,1/4,1/5])

sonified_C_Major_Triad_f0 = f0.sonify_f0(time_f0=time_f0,
                                         partials=custom_partials,
                                         partials_amplitudes=custom_partials_amplitudes,
                                         fs=Fs)

ipd.display(ipd.Audio(sonified_C_Major_Triad_f0, rate=Fs))

### __libsoni__ also offers the possibility to work with presets... In the following, we will present some examples

## F0 Trajectory for *Ach Gott und Herr by Bach* from Bach10 Dataset [1]

#### Load .csv files comprising the starting time points and f0s for each instrument

In [10]:
violin_df = pd.read_csv(os.path.join('data_csv','demo_f0','01-AchGottundHerr_violin.csv'), sep=';')
clarinet_df = pd.read_csv(os.path.join('data_csv','demo_f0','01-AchGottundHerr_clarinet.csv'), sep=';')
saxophone_df = pd.read_csv(os.path.join('data_csv','demo_f0','01-AchGottundHerr_saxophone.csv'), sep=';')
bassoon_df = pd.read_csv(os.path.join('data_csv','demo_f0','01-AchGottundHerr_bassoon.csv'), sep=';')
violin_df.iloc[100:105]

start          f0
100   1.00  494.484541
101   1.01  495.252512
102   1.02  498.796651
103   1.03  498.796651
104   1.04  498.796651

#### Sonify using presets *(for details, see libsoni/utils/presets.json)*

In [6]:
bach_dict = {'violin':violin_df.to_numpy(),
             'clarinet':clarinet_df.to_numpy(),
             'saxophone':saxophone_df.to_numpy(),
             'bassoon':bassoon_df.to_numpy()}

bach_audio, _ = librosa.load(os.path.join('data_audio','demo_f0','01-AchGottundHerr.wav'), sr=Fs)


bach_sonified = f0.sonify_f0_with_presets(bach_dict)

bach_sonified_w_original = mix_sonification_and_original(sonification=bach_sonified,
                                                         original_audio=bach_audio,
                                                         gain_lin_sonification=1.0,
                                                         gain_lin_original_audio=0.5)

print('Original recording')
ipd.display(ipd.Audio(bach_audio, rate=Fs))

print('Sonified with libsoni')
ipd.display(ipd.Audio(bach_sonified, rate=Fs))

print('Original audio with sonification (stereo)')
ipd.display(ipd.Audio(bach_sonified_w_original, rate=Fs))

Original recording


Sonified with libsoni


Original audio with sonification (stereo)


## SATB F0 Trajectory for *Locus Iste by Bruckner* from Dagstuhl Choirset [2]

In [11]:
soprano_df = pd.read_csv(os.path.join('data_csv','demo_f0','DCS_LI_QuartetA_Take04_S2_LRX.csv'), sep=';')
alto_df = pd.read_csv(os.path.join('data_csv','demo_f0','DCS_LI_QuartetA_Take04_A1_LRX.csv'), sep=';')
tenor_df = pd.read_csv(os.path.join('data_csv','demo_f0','DCS_LI_QuartetA_Take04_T1_LRX.csv'), sep=';')
bass_df = pd.read_csv(os.path.join('data_csv','demo_f0','DCS_LI_QuartetA_Take04_B1_LRX.csv'), sep=';')
soprano_df.iloc[100:105]

start       f0
100  0.580499  532.093
101  0.586304  531.004
102  0.592109  530.270
103  0.597914  529.670
104  0.603719  529.322

In [8]:
satb_dict = {'soprano':soprano_df.to_numpy(),
             'alto':alto_df.to_numpy(),
             'tenor':tenor_df.to_numpy(),
             'bass':bass_df.to_numpy()}

satb_audio, _ = librosa.load(os.path.join('data_audio','demo_f0','DCS_LI_QuartetA_Take04_StereoReverb_STM.wav'), sr=Fs)
satb_sonified = f0.sonify_f0_with_presets(satb_dict)
satb_sonified_w_original = mix_sonification_and_original(sonification=satb_sonified,
                                                         original_audio=satb_audio,
                                                         gain_lin_original_audio=0.05)

print('Original recording')
ipd.display(ipd.Audio(satb_audio, rate=Fs))

print('Sonified with libsoni')
ipd.display(ipd.Audio(satb_sonified, rate=Fs))

print('Original audio with sonification (stereo)')
ipd.display(ipd.Audio(satb_sonified_w_original, rate=Fs))

Original recording


Sonified with libsoni


Original audio with sonification (stereo)


## References

[1] Zhiyao Duan, Bryan Pardo and Changshui Zhang, “Multiple fundamental frequency estimation by modeling spectral peaks and non-peak regions,” IEEE Transactions of Audio Speech Language Process., vol. 18, no. 8, pp. 2121–2133, 2010.

[2] S. Rosenzweig, H. Cuesta, C. Weiß, F. Scherbaum, E. Gómez, and M. Müller, “Dagstuhl ChoirSet: A multitrack dataset for MIR research on choral singing,” Transactions of the International Society for Music Information Retrieval (TISMIR), vol. 3, no. 1, pp. 98–110, 2020.